In [7]:
import time
import random
import csv
import json
import re
from typing import List, Dict, Optional
import requests
from bs4 import BeautifulSoup
import pandas as pd
import numpy as np

In [8]:
ur1 ="https://www.forbes.com/lists/global2000/"
headers = { "User-Agent": "Mozilla/5.0"}

response=requests.get(ur1,headers=headers)
response

response = requests . get(ur1)
response

<Response [200]>

In [9]:
txt =response.text
txt[:100]

'<!DOCTYPE html><html lang="en"><head><link rel="preload" as="font" href="https://i.forbesimg.com/ass'

In [10]:
html_code=response.text
html_code[:100]

'<!DOCTYPE html><html lang="en"><head><link rel="preload" as="font" href="https://i.forbesimg.com/ass'

In [11]:
soup=BeautifulSoup(html_code)
soup

<!DOCTYPE html>
<html lang="en"><head><link as="font" crossorigin="" href="https://i.forbesimg.com/assets/fonts/Schnyder/Schnyder-SDemi-Web.woff2" rel="preload" type="font/woff2"/><link as="font" crossorigin="" href="https://i.forbesimg.com/assets/fonts/Graphik/Graphik-Medium-Web.woff2" rel="preload" type="font/woff2"/><link as="font" crossorigin="" href="https://i.forbesimg.com/assets/fonts/merriweather/merriweather-regular-webfont.woff2" rel="preload" type="font/woff2"/><link as="font" crossorigin="" href="https://i.forbesimg.com/assets/fonts/EuclidCircular/EuclidCircularB-Regular.otf" rel="preload" type="font/otf"/><link as="font" crossorigin="" href="https://i.forbesimg.com/assets/fonts/Schnyder/SchnyderCondL-Bold.otf" rel="preload" type="font/otf"/><link as="font" crossorigin="" href="https://i.forbesimg.com/assets/fonts/merriweather/merriweather-bold-webfont.woff2" rel="preload" type="font/woff2"/><link as="font" crossorigin="" href="https://i.forbesimg.com/assets/fonts/work-sans

In [12]:
soup.text[:300]

"Forbes' 2025 Global 2000 List - The World’s Largest Companies RankedNewslettersGamesShare a News TipFeaturedFeaturedBreaking NewsWhite House WatchDaily Cover StoriesThe Cloud 100 List  | Paid ProgramThe Employee Well-Being Imperative | Paid ProgramBest-In-State Top Next-Gen Wealth Advisors 2025AI’s "

In [59]:
title = soup.find('div',attrs={'class':'table-wrapper'})
title.text

"RANKNAMEHEADQUARTERSINDUSTRYSALES PROFIT ASSETS MARKET VALUE 1JPMorganChaseUnited StatesBanking$285.11 B$59.36 B$4,357.86 B$677.8 B2Berkshire HathawayUnited StatesInsurance$371.43 B$89 B$1,153.88 B$1,145.46 B3ICBCChinaBanking$221.96 B$50.84 B$6,688.6 B$251.33 B4Saudi Arabian Oil Company (Saudi Aramco)Saudi ArabiaOil & Gas Operations$480.15 B$104.97 B$645.03 B$1,663.38 B5AmazonUnited StatesRetail and Wholesale$637.96 B$59.25 B$624.89 B$2,005.64 B6Bank of AmericaUnited StatesBanking$196.53 B$27.85 B$3,349.42 B$300.06 B7China Construction BankChinaBanking$196.71 B$46.64 B$5,558.26 B$219.81 B8Agricultural Bank of ChinaChinaBanking$198.02 B$39.2 B$5,923.64 B$212.51 B9AlphabetUnited StatesIT Software & Services$359.31 B$111 B$475.37 B$1,973.64 B9MicrosoftUnited StatesIT Software & Services$261.8 B$92.75 B$533.9 B$2,913.01 B11AppleUnited StatesTechnology Hardware & Equipment$395.76 B$96.15 B$344.08 B$3,143.82 B12Bank of ChinaChinaBanking$177.05 B$32.3 B$4,855.83 B$164.71 B13ExxonMobilUnited 

In [21]:
# Set headers to mimic a browser request
headers = {
    "User-Agent": "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/120.0.0.0 Safari/537.36"
}

all_companies = []

# Forbes serves ~200 companies per page — fetch 5 pages = ~1000 companies
for page in range(1, 6):
    start = (page - 1) * 200
    url = f"https://www.forbes.com/forbesapi/org/global2000/2025/position/true.json?limit=200&start={start}"
 
    
    response = requests.get(url, headers=headers)
    if response.status_code != 200:
        print(f" Error {response.status_code} on page {page}")
        break

    data = response.json()
    org_list = data.get("organizationList", {})
    companies = org_list.get("organizationsLists", []) or org_list.get("organizations", [])

    if not companies:
        print(f" No data found on page {page}")
        continue

    for c in companies:
        all_companies.append({
            "Rank": c.get("rank"),
            "Name": c.get("organizationName"),
            "Country": c.get("country"),
            "Headquarters": c.get("hqLocation") or c.get("hq"),
            "Industry": c.get("industry"),
            "Sales": c.get("sales") or c.get("salesAmount") or c.get("revenue"),
            "Profits": c.get("profits"),
            "Assets": c.get("assets"),
            "Market Value": c.get("marketValue")
        })

    time.sleep(1)  # Be polite to the server

# Create DataFrame
df = pd.DataFrame(all_companies)




In [22]:
df

Rank                                               Name        Country  \
0       1                                      JPMorganChase  United States   
1       2                                 Berkshire Hathaway  United States   
2       3                                               ICBC          China   
3       4           Saudi Arabian Oil Company (Saudi Aramco)   Saudi Arabia   
4       5                                             Amazon  United States   
..    ...                                                ...            ...   
995   996                                              Dover  United States   
996   997                                   China Bohai Bank          China   
997   998  Commercial Bank For Investment & Development O...        Vietnam   
998   999                            China National Chemical          China   
999  1000                           Sunshine Insurance Group          China   

    Headquarters              Industry     Sales   Profits     Assets  \
0           None               Banking  285106.0   59358.0  4357856.0   
1           None             Insurance  371433.0   88995.0  1153881.0   
2           None               Banking  221963.0   50843.1  6688598.0   
3           None  Oil & Gas Operations  480146.0  104971.8   645028.0   
4           None  Retail and Wholesale  637959.0   59248.0   624894.0   
..           ...                   ...       ...       ...        ...   
995         None         Capital Goods    7958.0    2295.7    12649.0   
996         None               Banking    9147.0     730.1   253058.0   
997         None               Banking    6876.0     984.2   108330.0   
998         None          Construction   25213.0     768.9    32022.0   
999         None             Insurance   12182.0     757.1    79705.0   

     Market Value  
0        677800.0  
1       1145461.0  
2        251332.0  
3       1663384.0  
4       2005638.0  
..            ...  
995       23165.0  
996        2130.0  
997        9444.0  
998        6223.0  
999        6240.0  

[1000 rows x 9 columns]

In [23]:
df.drop(columns=["Headquarters"], inplace=True)


In [24]:
df.isnull().sum()

Rank            0
Name            0
Country         0
Industry        0
Sales           0
Profits         0
Assets          0
Market Value    0
dtype: int64

In [25]:
df.duplicated().sum()

np.int64(0)

In [27]:
# Save to CSV
df.to_csv("A_forbes_global_1000.csv", index=False)
